In [8]:
%cd ~/xls-r-uzbek-cv8

/workspace/xls-r-uzbek-cv8


In [10]:
!python -m pip install -r requirements.txt --user

  Using cached https://github.com/kpu/kenlm/archive/master.zip (541 kB)
  Preparing metadata (setup.py) ... done
  Using cached tensorboard-2.8.0-py3-none-any.whl (5.8 MB)
  Using cached transformers-4.16.2-py3-none-any.whl (3.5 MB)
  Using cached datasets-1.18.3-py3-none-any.whl (311 kB)
  Using cached google_auth_oauthlib-0.4.6-py2.py3-none-any.whl (18 kB)
  Created wheel for kenlm: filename=kenlm-0.0.0-cp38-cp38-linux_x86_64.whl size=2348591 sha256=d5c8e5430d89f59ddde39bc78aec471c1e66ef43b6cde792711b2e97d7b8b9dc
  Stored in directory: /tmp/pip-ephem-wheel-cache-hhcfnszu/wheels/ff/08/4e/a3ddc0e786e0f3c1fcd2e7a82c4324c02fc3ae2638471406d2
Successfully built kenlm
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-wa

In [14]:
from transformers import AutoFeatureExtractor, AutoTokenizer, pipeline
from datasets import Audio, Dataset, DatasetDict, load_dataset, load_metric

import re
import string
import unidecode

In [12]:
dataset_dict = load_dataset("mozilla-foundation/common_voice_8_0", "uz", use_auth_token=True)
dataset_dict

Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/uz/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)


  0%|          | 0/5 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'],
        num_rows: 39456
    })
    test: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'],
        num_rows: 11598
    })
    validation: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'],
        num_rows: 10849
    })
    other: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'],
        num_rows: 119461
    })
    invalidated: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'],
        num_rows: 11276
    })
})

In [17]:
chars_to_ignore_regex=f"[{re.escape(string.punctuation)}]" 

def remove_special_characters(batch):
    batch["text"] = re.sub(
        chars_to_ignore_regex, 
        "", 
        re.sub("['`´]", "’",   # elsewhere probably meant as glottal stop
               re.sub("([og])['`´]", "\g<1>‘",  # after o/g indicate modified char
                      unidecode.unidecode(batch["sentence"]).lower()
                     )
              )
    ) + " "
    return batch

In [18]:
dataset = dataset_dict["train"].map(remove_special_characters, remove_columns=dataset_dict["train"].column_names)

0ex [00:00, ?ex/s]

In [23]:
text_data = "uz_cv8_train.txt"
with open(text_data, "w") as fs:
    fs.write(" ".join(dataset["text"]))

!wc $text_data

      0  244494 2030240 uz_cv8_train.txt


In [26]:
!wget -O - https://kheafield.com/code/kenlm.tar.gz | tar xz
!mkdir kenlm/build && cd kenlm/build && cmake .. && make -j2


--2022-02-07 03:18:36--  https://kheafield.com/code/kenlm.tar.gz
Resolving kheafield.com (kheafield.com)... 35.196.63.85
Connecting to kheafield.com (kheafield.com)|35.196.63.85|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 491090 (480K) [application/x-gzip]
Saving to: ‘STDOUT’

-                   100%[===================>] 479.58K  2.31MB/s    in 0.2s    

2022-02-07 03:18:37 (2.31 MB/s) - written to stdout [491090/491090]

/bin/bash: line 1: cmake: command not found
